In [1]:
import numpy as np
import pandas as pd

In [2]:
trains_data = pd.read_csv('datasets/train.csv', lineterminator='\n')
review_id = trains_data.values[:, 0]
review = trains_data.values[:, 1]
label = trains_data.values[:, 2].copy()

In [3]:
id

<function id(obj, /)>

In [4]:
review

array(['Jo bhi ap se tou behtar hoon',
       'ya Allah meri sister Affia ki madad farma',
       'Yeh khud chahta a is umar main shadi krna.  had ogi', ...,
       'Korangi Me Shani Qatal ',
       'Ma na suna ha lemon sa haddiyan kamzor hoti hn regular Lana sa?',
       'Ball poar jadooi giraft se inhe rafter aur swing ko qaboo karne ka hairat angez fun aata hai'],
      dtype=object)

In [5]:
label

array(['Negative', 'Positive', 'Negative', ..., 'Negative', 'Negative',
       'Positive'], dtype=object)

In [6]:
label[trains_data.values[:, 2] == "Negative"] = 0
label[trains_data.values[:, 2] == "Positive"] = 1

In [7]:
label

array([0, 1, 0, ..., 0, 0, 1], dtype=object)

### 从文本中构建词条向量

In [8]:
import jieba as jb

In [9]:
seg_list = jb.cut(review[0])

In [10]:
seg_list = list(filter(lambda s: s and s.strip(), jb.lcut(review[0])))

Building prefix dict from the default dictionary ...
Loading model from cache C:\Users\zlm31\AppData\Local\Temp\jieba.cache
Loading model cost 0.819 seconds.
Prefix dict has been built succesfully.


In [11]:
seg_list

['Jo', 'bhi', 'ap', 'se', 'tou', 'behtar', 'hoon']

In [12]:
def cut_review(reviews):
    """将样本进行分词处理"""
    relist = []
    for review in reviews:
        relist.append(list(filter(lambda s: s and s.strip(), jb.lcut(review))))
    return relist


In [13]:
def load_datasets():
    relist = cut_review(review)
    return relist, label
review,label = load_datasets()

In [14]:
review

[['Jo', 'bhi', 'ap', 'se', 'tou', 'behtar', 'hoon'],
 ['ya', 'Allah', 'meri', 'sister', 'Affia', 'ki', 'madad', 'farma'],
 ['Yeh',
  'khud',
  'chahta',
  'a',
  'is',
  'umar',
  'main',
  'shadi',
  'krna',
  '.',
  'had',
  'ogi'],
 ['Tc',
  '?',
  'Apky',
  'mun',
  'xe',
  'exe',
  'alfax',
  'achy',
  'nae',
  'lgty',
  '😒',
  '💃'],
 ['Good'],
 ['American',
  'president',
  'John',
  'f',
  'Kennedy',
  'aur',
  'in',
  'ke',
  'bhai',
  'Robert',
  'Kennedy',
  'se',
  'bhi',
  'Marilyn',
  'Monroe',
  'ke',
  'affairs',
  'ka',
  'charcha',
  'raha'],
 ['Commission',
  'aur',
  'kickback',
  'ka',
  'dor',
  'Dora',
  'raha',
  ',',
  'quomi',
  'assase',
  'koriyon',
  'ke',
  'mol',
  'farokhat',
  'keye',
  'gaye'],
 ['Allah',
  'pak',
  'nazer',
  'e',
  'bd',
  'sy',
  'bechye',
  'or',
  'humesha',
  'bohat',
  'tarkian',
  'dy',
  'Ameeen'],
 ['Amoman',
  'log',
  'samajhte',
  'hain',
  'ke',
  'jhok',
  'siyal',
  'hi',
  'Abid',
  'Ali',
  'ki',
  'pheli',
  'serial',

In [15]:
label

array([0, 1, 0, ..., 0, 0, 1], dtype=object)

In [16]:
def create_vocab_list(dataSet):
    """将所有词条集合传入，得到一个所有不重复词条的集合字典"""
    vocabSet = set([])
    for document in dataSet:
        vocabSet = vocabSet | set(document)
    return list(vocabSet)

len(create_vocab_list(review))

21353

In [17]:
def setOfWords2Vec(vocabList, inputSet):
    returnVec = np.zeros(len(vocabList))
    for word in inputSet:
        if word in vocabList:
            returnVec[vocabList.index(word)] = 1
        else:
            print("该词条%s不在词条字典中，请更新词条字典" % word)
    return returnVec

In [26]:
vocabList = create_vocab_list(review)
trainMatrix = []
for r in review:
    trainMatrix.append(setOfWords2Vec(vocabList, r))

In [79]:
def trainNBO(trainMatrix, trainCategory):
    #记录词条向量的个数
    numTrainDocs = len(trainMatrix)
    #记录单个词条向量的长度即词条字典长度
    numWords = len(trainMatrix[0])
    #pPositive是所有词条向量中是Positive言论的概率
    pPositive = np.sum(trainCategory) / float(numTrainDocs)
    #初始化Negative/Positive词条分布总和向量
    p0Num = np.ones(numWords)
    p1Num = np.ones(numWords)
    #初始化Negative/Positive言论中词条总个数
    p0Denom = 2.0
    p1Denom = 2.0
    for i in range(numTrainDocs):
        if trainCategory[i] == 1:
            #如果为Positive言论，记录所有词条向量累加后的总向量及所有Positive言论中总词条个数
            p1Num += trainMatrix[i]
            p1Denom  += np.sum(trainMatrix[i])
        else:
            #如果为Negative言论，记录所有词条向量累加后的总向量及所有Negative言论中总词条个数
            p0Num += trainMatrix[i]
            p0Denom += np.sum(trainMatrix[i])
        
    p1Vect = p1Num / p1Denom
    p0Vect = p0Num / p0Denom
    
    #对每个元素取对数
    for i in range(len(p1Vect)):
        p1Vect[i] = np.log(p1Vect[i])
        p0Vect[i] = np.log(p0Vect[i])
        
    return pPositive, p1Vect, p0Vect
    

In [80]:
pPos, p1V, p0V = trainNBO(np.array(trainMatrix), label)

In [81]:
pPos

0.5311314791403287

In [82]:
p1V

array([-10.14929239, -10.14929239, -10.84243957, ..., -10.84243957,
       -10.84243957, -10.84243957])

In [83]:
p0V

array([-9.96880702, -9.96880702, -9.96880702, ..., -9.96880702,
       -9.27565984, -9.96880702])

In [84]:
def NBClassifier(vec2Classify, p0Vec, p1Vec, pPositive):
    p1 = np.sum(vec2Classify * p1Vec) + np.log(pPositive)
    p0 = np.sum(vec2Classify * p0Vec) + np.log(1.0 - pPositive)
    if p1 > p0:
        return 1
    else:
        return 0

In [ ]:
temp = []
for i in range(len(review)):
    temp.append(NBClassifier(trainMatrix[i], p0V, p1V, pPos))

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

...

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条1.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条字典中，请更新词条字典
该词条0.0不在词条

In [ ]:
np.sum(np.array(temp) == np.array(label)) / len(label)

### 测试模型

In [73]:
test_data = pd.read_csv('datasets/test.csv', lineterminator='\n')
review_id = trains_data.values[:, 0]
review = trains_data.values[:, 1]

In [74]:
testMatrix = []
relist = cut_review(review)
for r in relist:
    testMatrix.append(setOfWords2Vec(vocabList, r))

In [75]:
result = []
for x in testMatrix:
    result.append(NBClassifier(x, p0V, p1V, pPos))

In [76]:
result

[0.011734614073995451,
 0.01418538303104229,
 0.010436537295898609,
 0.0009553845086792758,
 0.0004153845689909894,
 0.03305422707745799,
 0.025753843277441343,
 0.009377306644971585,
 0.051289609656162416,
 0.010145768097604918,
 0.0014330767630189136,
 0.019429613214553533,
 0.0008203845237572042,
 0.040313072420575524,
 0.01740461344072246,
 0.00013499998492207157,
 0.017788844167039124,
 0.01118422952008239,
 0.00048807686856441255,
 0.021371536074586413,
 0.002575384327744134,
 0.03193268874118232,
 0.01739422882649768,
 0.00988615274198555,
 0.014798075270303997,
 0.014756536813404898,
 0.02635615090247828,
 0.05303422484592458,
 0.0072484607288927656,
 0.00942922971609546,
 0.009834229670861677,
 0.032181919482576905,
 3.115384267432421e-05,
 0.011381537190353112,
 0.008619229806563032,
 0.06809191547184795,
 0.007269229957342315,
 0.06870460771110966,
 0.0013499998492207158,
 0.0005711537823626105,
 0.004849614842969802,
 0.041102303101658404,
 0.022960382050976943,
 0.02903538

In [77]:
data = {'ID': review_id, 'Pred': result}
df = pd.DataFrame(data, columns=['ID', 'Pred'])
print(df)

        ID      Pred
0        1  0.011735
1        2  0.014185
2        3  0.010437
3        4  0.000955
4        5  0.000415
5        6  0.033054
6        7  0.025754
7        8  0.009377
8        9  0.051290
9       10  0.010146
10      11  0.001433
11      12  0.019430
12      13  0.000820
13      14  0.040313
14      15  0.017405
15      16  0.000135
16      17  0.017789
17      18  0.011184
18      19  0.000488
19      20  0.021372
20      21  0.002575
21      22  0.031933
22      23  0.017394
23      24  0.009886
24      25  0.014798
25      26  0.014757
26      27  0.026356
27      28  0.053034
28      29  0.007248
29      30  0.009429
...    ...       ...
6298  6299  0.000810
6299  6300  0.022109
6300  6301  0.023345
6301  6302  0.021517
6302  6303  0.000737
6303  6304  0.000976
6304  6305  0.012119
6305  6306  0.002087
6306  6307  0.003583
6307  6308  0.006760
6308  6309  0.000758
6309  6310  0.010104
6310  6311  0.020821
6311  6312  0.034508
6312  6313  0.013832
6313  6314  0

In [78]:
df.to_csv('datasets/result.csv',index=False)